In [52]:
%pip install langgraph

In [53]:
%pip install langchain-google-genai

In [82]:
import pandas as pd
from langgraph.graph import StateGraph, END
from langchain_core.prompts import ChatPromptTemplate
from langchain_google_genai import ChatGoogleGenerativeAI
import os

In [93]:
os.environ["GOOGLE_API_KEY"] = "API KEY"

llm = ChatGoogleGenerativeAI(
    model="gemini-2.5-flash",
    temperature=0.2
)


In [84]:
prompt = ChatPromptTemplate.from_template("""
You are a sentiment analysis model.
Given the text: "{text}", classify it as Positive, Negative.
Also give your confidence score (a value between 0 and 1).
Example output:
Sentiment: Positive
Confidence: 0.92
""")

In [85]:
def llm_sentiment_node(state):
    text = state["text"]
    print(f"\nAnalyzing: '{text[:60]}...'")
    response = llm.invoke(prompt.format(text=text))
    result = response.content.strip()
    sentiment, confidence = "Unknown", 0.0
    for line in result.split("\n"):
        if "sentiment" in line.lower():
            sentiment = line.split(":")[-1].strip()
        elif "confidence" in line.lower():
            try:
                confidence = float(line.split(":")[-1].strip())
            except ValueError:
                confidence = 0.0

    state["sentiment"] = sentiment
    state["confidence"] = confidence
    return state

In [86]:
def store_result_node(state):
    results.append({
        "Text": state["text"],
        "Final Sentiment": state["sentiment"],
        "Confidence": state["confidence"]
    })
    print(f"Stored → Sentiment: {state['sentiment']} (Confidence: {state['confidence']:.2f})")
    return state

In [87]:
def human_feedback_node(state):
    print(f"\nHuman review triggered!")
    print(f"Low confidence ({state['confidence']:.2f}) for text:\n {state['text']}")
    user_input = input("Enter correct sentiment (Positive / Negative): ").strip()
    state["sentiment"] = user_input if user_input else "ReviewNeeded"
    state["confidence"] = 1.0
    print(f"Human feedback recorded: {state['sentiment']}")
    return state


In [88]:
workflow = StateGraph(dict)

workflow.add_node("llm_sentiment", llm_sentiment_node)
workflow.add_node("human_feedback", human_feedback_node)
workflow.add_node("store_result", store_result_node)

workflow.set_entry_point("llm_sentiment")

In [89]:
def decision_router(state):
    if state["confidence"] < 0.95:
        return "human_feedback"
    else:
        return "store_result"


In [90]:
workflow.add_conditional_edges("llm_sentiment", decision_router)
workflow.add_edge("human_feedback", "store_result")
workflow.add_edge("store_result", END)

app = workflow.compile()


In [91]:
df = pd.read_csv('/content/test.csv')
texts_to_process = df.iloc[:, 0].dropna().tolist()

In [94]:
print("\nStarting Sentiment Analysis Workflow using Gemini + LangGraph\n")

results = []
for text in texts_to_process:
    app.invoke({"text": text})


output_df = pd.DataFrame(results)
output_filename = "sentiment_results_from_csv.csv"
output_df.to_csv(output_filename, index=False)

print("\n Analysis Complete")
print(f"Results saved to: {output_filename}")
print(f"\nSample output:\n{output_df.head()}")


Starting Sentiment Analysis Workflow using Gemini + LangGraph


Analyzing: 'The new update made the app so much better!...'
Stored → Sentiment: Positive (Confidence: 0.98)

Analyzing: 'I am really disappointed with the quality of this item....'
Stored → Sentiment: Negative (Confidence: 0.99)

Analyzing: 'It works fine, but nothing exceptional....'

Human review triggered!
Low confidence (0.70) for text:
 It works fine, but nothing exceptional.
Enter correct sentiment (Positive / Negative): Positive
Human feedback recorded: Positive
Stored → Sentiment: Positive (Confidence: 1.00)

Analyzing: 'Customer support was outstanding and resolved my issue quick...'
Stored → Sentiment: Positive (Confidence: 0.98)

Analyzing: 'The packaging was terrible, and the product arrived damaged....'
Stored → Sentiment: Negative (Confidence: 0.99)

Analyzing: 'Overall, it's an average experience, could be improved....'

Human review triggered!
Low confidence (0.90) for text:
 Overall, it's an average exper